## Imports

In [1]:
from selenium import webdriver
from selenium.webdriver.chrome.service import Service as ChromeService
from selenium.webdriver.chrome.options import Options
import time
from bs4 import BeautifulSoup

import pandas as pd

## Load Data

In [2]:
fulltime = pd.read_csv("dice_scraped_7_days_full_time.csv")
contract = pd.read_csv("dice_scraped_7_days_contract.csv")

df = pd.concat([fulltime, contract])

print(f"The length of combined dataframe is: {len(fulltime)}")
print(f"The length of combined dataframe is: {len(contract)}")
print(f"The length of combined dataframe is: {len(df)}")

df['Link'].head()

The length of combined dataframe is: 10000
The length of combined dataframe is: 7128
The length of combined dataframe is: 17128


0    https://www.dice.com/job-detail/f3588c6f-5d1b-...
1    https://www.dice.com/job-detail/a84803c1-00e1-...
2    https://www.dice.com/job-detail/3b36a04f-0757-...
3    https://www.dice.com/job-detail/fcc3fce9-2ea1-...
4    https://www.dice.com/job-detail/d06c8f82-0a3f-...
Name: Link, dtype: object

## Split The Dataframe
Scraping data from a large number of URLs simultaneously can be computationally intensive and time-consuming. To optimize this process, we can break down the larger DataFrame into smaller subsets, each containing URLs, and then perform the scraping operation on each subset individually. This approach allows for better resource management and efficient data collection.

In [ ]:
# Split the fulltime DataFrame into 10 smaller DataFrames
#split_dfs = []
#batch_length = 1000
#for i in range(0, len(fulltime), batch_length):
    #batch_df = fulltime[i: i+batch_length]
    #split_dfs.append(batch_df)
    
#for idx, small_df in enumerate(split_dfs):
    #small_df.to_csv(f"fulltime_df_{idx}.csv", index=False)

In [ ]:
# Load the dataset
#sample_df = pd.read_csv("fulltime_df_#.csv")

# Content Scraping

In [3]:
# Set up Chrome WebDriver with options, including incognito mode
chrome_options = Options()
chrome_options.add_argument("--headless")  # Run in headless mode (no visible browser window)
chrome_options.add_argument("--incognito")  # Enable incognito mode

# Specify the path to your Chrome WebDriver executable
chrome_driver_path = r"C:\Users\sarvin.farhad\Data-Science\Projects\EquiJob\task-1-data-collection\chromedriver.exe"

# Set up the Chrome driver
service = ChromeService(executable_path=chrome_driver_path)
driver = webdriver.Chrome(service=service, options=chrome_options)

In [4]:
# Set the dataframe of urls (It could be fulltime, contract, combined df
# or even each samller dfs that is made of from splitting larger df)
sample_df = contract

# Initialize an empty DataFrame with columns
final_df = pd.DataFrame(columns=['url', 'title', 'company_name', 'location', 'description'])

# The size of batch can be adjusted based on the system's capabilities
batch_size = 200

# Calculate the number of batches
num_batches = len(df) // batch_size + 1

for batch in range(num_batches):
    start_idx = batch * batch_size
    end_idx = min((batch + 1) * batch_size, len(sample_df))  # Ensure it doesn't go beyond the end of the DataFrame
    
    # Slice the DataFrame to get the current batch
    current_batch = sample_df.iloc[start_idx:end_idx]

    for idx, row in current_batch.iterrows():
        url = row['Link']
        
        try:
            driver.get(url)
            
            # Wait for the page to load (you can adjust the wait time as needed)
            time.sleep(5)
            
            # Get the page source
            page_source = driver.page_source
            
            # Now you can parse the page_source with BeautifulSoup
            soup = BeautifulSoup(page_source, 'lxml')
        
            title = soup.find('h1', class_='mb-1').text
        
            job_info = soup.find('div', class_='job-info') #including company name, salary range and location
        
            detailed_info = job_info.find_all('li')
        
            [company_name, location] = [detailed_info[0].text, detailed_info[1].text]
        
            description = soup.find('section', class_='job-description').text

            # Assign values to the DataFrame using .loc[]
            final_df.loc[idx] = [url, title, company_name, location, description]

            # Print the progress
            print(f"Scraped URL #{idx + 1} ({url})")
        
        except Exception as e:
            print(f"Error scraping URL #{idx + 1} ({url}): {str(e)}")
        
# Close the browser when done
driver.quit()

Scraped URL #1 (https://www.dice.com/job-detail/94794f89-2ed4-4f00-834f-fc4b378aad0f?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D161%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=d53882ec-5fab-48d1-b870-d51275b7a1ef)
Error scraping URL #2 (https://www.dice.com/job-detail/bfe848dc-9d31-4d71-b380-bf623826a059?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D195%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=3842ed96-a63d-45b0-9619-4d2dcc427c48): 'NoneType' object has no attribute 'text'
Scraped URL #3 (https://www.dice.com/job-detail/1e747183-1d30-4495-b74d-f278807bafd7?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D179%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=66c8f480-73cf-49dd-9cb8-8fd8de86ac00)
Scrap

Scraped URL #27 (https://www.dice.com/job-detail/6310884b-34f1-4275-8f7c-c56b7a9cccfb?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D300%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=082433d6-262b-47b5-a506-82991cc29761)
Scraped URL #28 (https://www.dice.com/job-detail/a6fa0567-bd10-467c-a180-d4f7eaa1bce7?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D20%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=34499fb2-1ddc-4cac-adc4-21a37858dd35)
Error scraping URL #29 (https://www.dice.com/job-detail/028572ef-cba7-41d8-a15a-71701d8e38f7?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D121%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=366b519f-bb9a-492e-be23-63af4878f46d): 'NoneType' object has no attribute 'text'
Scr

Error scraping URL #52 (https://www.dice.com/job-detail/f49b0c4a-252a-40bb-ad90-353367760530?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D21%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=46c96963-0722-4d3e-a735-e8a67c66f86f): 'NoneType' object has no attribute 'text'
Scraped URL #53 (https://www.dice.com/job-detail/a56142f9-d425-4e15-94bc-8ce736f88043?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D357%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=975d7cdc-7121-4631-b039-7b9a0cc92ec7)
Scraped URL #54 (https://www.dice.com/job-detail/58f21fb2-8bd3-49b0-a44e-5c9e4258771e?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D33%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=533c4b2f-abc9-43a9-84f7-73d8c9aeb4d8)
Scra

Scraped URL #78 (https://www.dice.com/job-detail/47c986c1-44dc-40c8-84e9-ba49b89a8897?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D225%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=412fb583-52ab-41a3-88d2-e25c6f0e97fb)
Scraped URL #79 (https://www.dice.com/job-detail/9bc21a52-29a1-42f4-9ed3-00959829456e?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D201%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=a9266fd8-2ff0-4920-b1a2-3a6003b24b8d)
Scraped URL #80 (https://www.dice.com/job-detail/f5af13d1-85d4-4d42-a6b6-57577b70694e?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D326%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=fa984f00-2c27-4261-9631-9d55cc2f1169)
Scraped URL #81 (https://www.dice.com/job-detail/e6c

Error scraping URL #104 (https://www.dice.com/job-detail/931fa298-3d68-48e3-801d-0e5aad11588f?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D121%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=366b519f-bb9a-492e-be23-63af4878f46d): 'NoneType' object has no attribute 'text'
Error scraping URL #105 (https://www.dice.com/job-detail/55b55eb7-7ef0-4916-a626-13ba276f6ea5?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D329%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=274d8784-6225-4825-bfd7-c157008f15e9): 'NoneType' object has no attribute 'text'
Scraped URL #106 (https://www.dice.com/job-detail/bc8e032d-6147-4761-bac9-8c1ff02d2748?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D168%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3

...

Scraped URL #7023 (https://www.dice.com/job-detail/0bb084b6-9a85-4c05-8f63-912a7f9a686c?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D252%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=aee4e7ba-5d7b-4b26-9df4-bfcb8f54542e)
Scraped URL #7024 (https://www.dice.com/job-detail/3bc73e08-c042-4758-8609-87c813f17eab?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D344%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=71302ebd-41da-481c-a9cc-e1c90aa0192b)
Scraped URL #7025 (https://www.dice.com/job-detail/c90bb712-9459-4e6f-9843-a71da17f2cee?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D70%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=3186a0db-65b1-4b3a-90a7-35b735ba01cf)
Scraped URL #7026 (https://www.dice.com/job-det

Scraped URL #7048 (https://www.dice.com/job-detail/6656726e-1ec5-4f36-af4a-2233bdaefac9?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D323%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=bebd3fd2-6cc9-4d35-abca-4839bcd2553d)
Scraped URL #7049 (https://www.dice.com/job-detail/ac51d02d-e8df-4054-a73a-c56a2fb7fb5c?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D6%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=6efade27-28a8-4777-905a-cb501e5ba959)
Scraped URL #7050 (https://www.dice.com/job-detail/93ab4b19-82ac-4327-aa4a-965b53879d45?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D327%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=1df54a43-a806-4fe8-a5c3-166a3c073b78)
Scraped URL #7051 (https://www.dice.com/job-deta

Error scraping URL #7073 (https://www.dice.com/job-detail/f76aa4ab-9b7a-4907-a9c8-5ea9f5fb3cc5?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D169%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=292f2375-783a-41e5-aa44-3e6e811ee6de): 'NoneType' object has no attribute 'text'
Error scraping URL #7074 (https://www.dice.com/job-detail/2ea22214-2e43-4c62-998d-58a93f88df23?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D14%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=648d0324-afe3-4015-97d7-1a420bff2493): 'NoneType' object has no attribute 'text'
Scraped URL #7075 (https://www.dice.com/job-detail/326e26bf-4938-48cb-b97d-4950cd9317bf?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D175%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language

Scraped URL #7098 (https://www.dice.com/job-detail/45779c4a-d04d-476f-9162-9a82793ab4ea?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D356%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=66d895d1-9069-4bf0-9506-c1d50518c922)
Scraped URL #7099 (https://www.dice.com/job-detail/1d69f355-eb8d-435f-8f9d-4afb28648482?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D53%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=1fb45807-01e7-4034-bd99-ea282891a8a7)
Scraped URL #7100 (https://www.dice.com/job-detail/e54af151-953e-48a3-bb9a-b29466a12ecf?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D23%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=f89f2453-4fca-4ebe-8ef6-4b600a5889c7)
Scraped URL #7101 (https://www.dice.com/job-deta

Scraped URL #7124 (https://www.dice.com/job-detail/a12e26bc-fdd4-4f8f-b8ac-4d42330f3a9f?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D21%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=46c96963-0722-4d3e-a735-e8a67c66f86f)
Scraped URL #7125 (https://www.dice.com/job-detail/29320192-d910-481f-a10d-5067e94aa625?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D141%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=f5268778-7af8-4794-9333-d13089c0e31a)
Error scraping URL #7126 (https://www.dice.com/job-detail/210b90a5-0340-4e8a-aff1-25853963ba15?searchlink=search%2F%3FcountryCode%3DUS%26radius%3D30%26radiusUnit%3Dmi%26page%3D344%26pageSize%3D20%26filters.postedDate%3DSEVEN%26filters.employmentType%3DCONTRACTS%26language%3Den&searchId=71302ebd-41da-481c-a9cc-e1c90aa0192b): 'NoneType' object has no attribute 'tex

## Save The Final Dataframe

In [6]:
# Check the final dataframe size
print(f"The length of final dataset is: {len(final_df)}")
final_df.head()

The length of final dataset is: 4302


url  \
0  https://www.dice.com/job-detail/94794f89-2ed4-...   
2  https://www.dice.com/job-detail/1e747183-1d30-...   
3  https://www.dice.com/job-detail/2cb8b0c9-92a8-...   
4  https://www.dice.com/job-detail/c2aa92af-a996-...   
5  https://www.dice.com/job-detail/fb7f7885-3d75-...   

                                               title  \
0          Software Engineer (W2 Only) (Local in MN)   
2  Power BI Modeler ,Juno Beach, Florida (Day one...   
3                   PeopleSoft Financials Consultant   
4  OneStream consultant with ( Planning and Conso...   
5                                Front End Developer   

                       company_name             location  \
0  Performix Business Services, LLC       Saint Paul, MN   
2              IT Trailblazers, LLC  Juno Beach, Florida   
3    Sligo Software Solutions Inc.,           Albany, NY   
4                          W3Global            Miami, FL   
5               Radiant System, Inc           Newark, CA   

                                         description  
0  Job DescriptionOur Client is seeking a Softwar...  
2  Job DescriptionJob Title: Power BI ModelerJob ...  
3  Job DescriptionGreetings from  Sligo Software ...  
4  Job DescriptionDescription:Have experience wit...  
5  Job DescriptionTitle: Front-end Developer   Lo...

In [7]:
# Save the final dataframe
final_df.to_csv("final_contract_dataset.csv")